In [2]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import log_loss, accuracy_score
import optuna
import lightgbm as lgb
import sklearn
import numpy as np
import matplotlib.pyplot as plt

c:\ProgramData\Anaconda3\lib\site-packages\dask\dataframe\utils.py:15: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [45]:
# read the data from /input/train.csv
data = pd.read_csv("train.csv")

In [46]:
X = data.drop(['Class', 'id'], axis=1)
y = data['Class']

In [47]:
X.head()

Mean_Integrated         SD        EK  Skewness  Mean_DMSNR_Curve  \
0       133.171875  59.716081  0.043133 -0.703383         54.917224   
1        87.093750  36.257973  0.435469  2.266057          3.417224   
2       112.640625  39.818393  0.379639  0.922306          2.730769   
3       120.679688  45.918448 -0.098490  0.011775          2.696488   
4       134.070312  57.720107 -0.107772 -0.573335          1.107860   

   SD_DMSNR_Curve  EK_DMSNR_Curve  Skewness_DMSNR_Curve  
0       70.084438        0.749798             -0.649512  
1       21.865069        7.039330             52.686251  
2       15.689690        8.193471             85.649785  
3       20.954662        8.183874             70.332899  
4       11.255051       16.107748            308.753765

# Preprocessing with PolynomialFeatures!!!

In [8]:
# preprocess the data by adding interaction features
#from sklearn.preprocessing import PolynomialFeatures
#poly = PolynomialFeatures(2, interaction_only=True, include_bias=False)
#X = poly.fit_transform(X)

# Train, Val, Test Split

In [48]:
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.1, random_state=42)
X_train, X_val, y_train, y_val = train_test_split(
    X_train, y_train, test_size=0.11, random_state=42)

In [49]:
X_train.shape

(94168, 8)

# Parameter search with Optuna

In [50]:
def objective(trial): 
    params = {
    'task': 'train', 
    'boosting_type':'gbdt',
    'objective':'binary',
    'metric':'binary_logloss', 
    'verbose':-10000000,
    'seed':42,
    'max_bin':128,
    #'n_estimators':128,
    'n_estimators':trial.suggest_int("n_estimators", 64, 1024),
    'learning_rate':trial.suggest_loguniform("learning_rate", 0.01, 0.1),
    'feature_fraction':trial.suggest_uniform("feature_fraction", 0.5, 1.0),
    'bagging_fraction':trial.suggest_uniform("bagging_fraction", 0.5, 1.0),
    #'bagging_freq':trial.suggest_categorical("bagging_freq", [1]),
    'max_depth':trial.suggest_int("max_depth", 3, 8), # decrease this in the next round
    'num_leaves':trial.suggest_int("num_leaves",8, 32),
    'min_data_in_leaf':trial.suggest_int("min_data_in_leaf", 64, 256),
    'min_gain_to_split':trial.suggest_loguniform("min_gain_to_split", 0.001, 1.0),
}
    
    model = lgb.LGBMClassifier(**params)
    model.fit(X_train, y_train, eval_set=[(X_val, y_val)], early_stopping_rounds=100)
    y_val_pred = model.predict_proba(X_val)
    logloss = log_loss(y_val, y_val_pred)
    return logloss

In [51]:
study = optuna.create_study(direction='minimize');
study.optimize(objective, n_trials=250);
#optuna.visualization.plot_optimization_history(study)


[I 2023-03-13 21:53:07,798] A new study created in memory with name: no-name-4def43b9-ad46-4ec2-bdd0-ec23e4ba8054
c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:12: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  if sys.path[0] == "":
c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:13: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  del sys.path[0]
c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:14: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float

[LightGBM] [Warning] feature_fraction is set=0.6943443554349615, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6943443554349615
[LightGBM] [Warning] min_data_in_leaf is set=217, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=217
[LightGBM] [Warning] min_gain_to_split is set=0.7514617786691214, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.7514617786691214
[LightGBM] [Warning] bagging_fraction is set=0.7005802841809892, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7005802841809892
[1]	valid_0's binary_logloss: 0.299016
[2]	valid_0's binary_logloss: 0.283842
[3]	valid_0's binary_logloss: 0.271095
[4]	valid_0's binary_logloss: 0.259669
[5]	valid_0's binary_logloss: 0.249492
[6]	valid_0's binary_logloss: 0.240313
[7]	valid_0's binary_logloss: 0.231957
[8]	valid_0's binary_logloss: 0.224419
[9]	valid_0's binary_logloss: 0.217281
[10]	valid_0's binary_logloss: 0.210647
[11]	valid_0's binary_logloss:

[I 2023-03-13 21:53:09,618] Trial 0 finished with value: 0.03384432192892599 and parameters: {'n_estimators': 752, 'learning_rate': 0.01993713669571654, 'feature_fraction': 0.6943443554349615, 'bagging_fraction': 0.7005802841809892, 'max_depth': 7, 'num_leaves': 20, 'min_data_in_leaf': 217, 'min_gain_to_split': 0.7514617786691214}. Best is trial 0 with value: 0.03384432192892599.


[487]	valid_0's binary_logloss: 0.0339025
[488]	valid_0's binary_logloss: 0.0339025
[489]	valid_0's binary_logloss: 0.0339025
[490]	valid_0's binary_logloss: 0.0339025
[491]	valid_0's binary_logloss: 0.0339025
[492]	valid_0's binary_logloss: 0.0339025
[493]	valid_0's binary_logloss: 0.0339025
[494]	valid_0's binary_logloss: 0.0339025
[495]	valid_0's binary_logloss: 0.0339025
[496]	valid_0's binary_logloss: 0.0339025
[497]	valid_0's binary_logloss: 0.0339025
[498]	valid_0's binary_logloss: 0.0339025
[499]	valid_0's binary_logloss: 0.0339025
[500]	valid_0's binary_logloss: 0.0339025
[501]	valid_0's binary_logloss: 0.0339025
[502]	valid_0's binary_logloss: 0.0339025
[503]	valid_0's binary_logloss: 0.0339025
[504]	valid_0's binary_logloss: 0.0339025
[505]	valid_0's binary_logloss: 0.0339025
[506]	valid_0's binary_logloss: 0.0339025
[507]	valid_0's binary_logloss: 0.0339025
[508]	valid_0's binary_logloss: 0.0339025
[509]	valid_0's binary_logloss: 0.0339025
[510]	valid_0's binary_logloss: 0.

c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:12: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  if sys.path[0] == "":
c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:13: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  del sys.path[0]
c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:14: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  
c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:19: FutureWarning: suggest_logunifo

...

[419]	valid_0's binary_logloss: 0.0335544
[420]	valid_0's binary_logloss: 0.033554
[421]	valid_0's binary_logloss: 0.0335539
[422]	valid_0's binary_logloss: 0.0335516
[423]	valid_0's binary_logloss: 0.0335544
[424]	valid_0's binary_logloss: 0.0335674
[425]	valid_0's binary_logloss: 0.0335734
[426]	valid_0's binary_logloss: 0.0335677
[427]	valid_0's binary_logloss: 0.0335819
[428]	valid_0's binary_logloss: 0.0335842
[429]	valid_0's binary_logloss: 0.0335883
[430]	valid_0's binary_logloss: 0.0335792
[431]	valid_0's binary_logloss: 0.0335897
[432]	valid_0's binary_logloss: 0.0335888
[433]	valid_0's binary_logloss: 0.0335921
[434]	valid_0's binary_logloss: 0.033593
[435]	valid_0's binary_logloss: 0.0335956
[436]	valid_0's binary_logloss: 0.0335902
[437]	valid_0's binary_logloss: 0.0335984
[438]	valid_0's binary_logloss: 0.0336076
[439]	valid_0's binary_logloss: 0.0336095
[440]	valid_0's binary_logloss: 0.0336138
[441]	valid_0's binary_logloss: 0.0336031
[442]	valid_0's binary_logloss: 0.03

c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:12: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  if sys.path[0] == "":
c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:13: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  del sys.path[0]
c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:14: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  
c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:19: FutureWarning: suggest_logunifo

[LightGBM] [Warning] feature_fraction is set=0.8795643964857007, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8795643964857007
[LightGBM] [Warning] min_data_in_leaf is set=247, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=247
[LightGBM] [Warning] min_gain_to_split is set=0.049398818023659787, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.049398818023659787
[LightGBM] [Warning] bagging_fraction is set=0.7557525939459123, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7557525939459123
[1]	valid_0's binary_logloss: 0.263573
[2]	valid_0's binary_logloss: 0.232875
[3]	valid_0's binary_logloss: 0.210458
[4]	valid_0's binary_logloss: 0.192582
[5]	valid_0's binary_logloss: 0.177746
[6]	valid_0's binary_logloss: 0.165103
[7]	valid_0's binary_logloss: 0.15411
[8]	valid_0's binary_logloss: 0.14452
[9]	valid_0's binary_logloss: 0.135875
[10]	valid_0's binary_logloss: 0.128123
[11]	valid_0's binary_loglos

[I 2023-03-13 21:57:47,776] Trial 249 finished with value: 0.03361952654888354 and parameters: {'n_estimators': 892, 'learning_rate': 0.06032389609365344, 'feature_fraction': 0.8795643964857007, 'bagging_fraction': 0.7557525939459123, 'max_depth': 3, 'num_leaves': 30, 'min_data_in_leaf': 247, 'min_gain_to_split': 0.049398818023659787}. Best is trial 246 with value: 0.03338523127850006.


[485]	valid_0's binary_logloss: 0.0336767
[486]	valid_0's binary_logloss: 0.0336768
[487]	valid_0's binary_logloss: 0.0336704
[488]	valid_0's binary_logloss: 0.0336766
[489]	valid_0's binary_logloss: 0.0336839
[490]	valid_0's binary_logloss: 0.0336852
[491]	valid_0's binary_logloss: 0.033692
[492]	valid_0's binary_logloss: 0.0336926
[493]	valid_0's binary_logloss: 0.0337023
[494]	valid_0's binary_logloss: 0.0337142
[495]	valid_0's binary_logloss: 0.0337285
[496]	valid_0's binary_logloss: 0.0337265
[497]	valid_0's binary_logloss: 0.0337267
[498]	valid_0's binary_logloss: 0.0337259
[499]	valid_0's binary_logloss: 0.0337223
[500]	valid_0's binary_logloss: 0.0337094
[501]	valid_0's binary_logloss: 0.0337117
[502]	valid_0's binary_logloss: 0.0337095
[503]	valid_0's binary_logloss: 0.0337081
[504]	valid_0's binary_logloss: 0.0337166
[505]	valid_0's binary_logloss: 0.0337298
[506]	valid_0's binary_logloss: 0.033719
[507]	valid_0's binary_logloss: 0.0337336
[508]	valid_0's binary_logloss: 0.03

In [52]:
study.best_trial.params

{'n_estimators': 918,
 'learning_rate': 0.08458168406863444,
 'feature_fraction': 0.8920419100694292,
 'bagging_fraction': 0.7441620142096533,
 'max_depth': 3,
 'num_leaves': 30,
 'min_data_in_leaf': 243,
 'min_gain_to_split': 0.037469004918636514}

In [53]:
params = {
    'task': 'train', 
    'boosting_type':'gbdt',
    'objective':'binary',
    'metric':'binary_logloss', 
    'verbose':-10000000,
    'seed':42,
    'max_bin':128,
}

In [54]:
params.update(study.best_trial.params)

In [74]:
print(params)

{'task': 'train', 'boosting_type': 'gbdt', 'objective': 'binary', 'metric': 'binary_logloss', 'verbose': -10000000, 'seed': 42, 'max_bin': 128, 'n_estimators': 918, 'learning_rate': 0.08458168406863444, 'feature_fraction': 0.8920419100694292, 'bagging_fraction': 0.7441620142096533, 'max_depth': 3, 'num_leaves': 30, 'min_data_in_leaf': 243, 'min_gain_to_split': 0.037469004918636514}


In [60]:
tuned_model = lgb.LGBMClassifier(**params)
tuned_model.fit(X_train, y_train, 
        eval_set=[(X_val, y_val)],
        eval_metric=['binary_logloss'],
        early_stopping_rounds=100) 

c:\ProgramData\Anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "


[LightGBM] [Warning] feature_fraction is set=0.8920419100694292, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8920419100694292
[LightGBM] [Warning] min_data_in_leaf is set=243, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=243
[LightGBM] [Warning] min_gain_to_split is set=0.037469004918636514, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.037469004918636514
[LightGBM] [Warning] bagging_fraction is set=0.7441620142096533, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7441620142096533
[1]	valid_0's binary_logloss: 0.243295
[2]	valid_0's binary_logloss: 0.209137
[3]	valid_0's binary_logloss: 0.18504
[4]	valid_0's binary_logloss: 0.166261
[5]	valid_0's binary_logloss: 0.150956
[6]	valid_0's binary_logloss: 0.138131
[7]	valid_0's binary_logloss: 0.127177
[8]	valid_0's binary_logloss: 0.117746
[9]	valid_0's binary_logloss: 0.109343
[10]	valid_0's binary_logloss: 0.101872
[11]	valid_0's binary_loglo

LGBMClassifier(bagging_fraction=0.7441620142096533,
               feature_fraction=0.8920419100694292,
               learning_rate=0.08458168406863444, max_bin=128, max_depth=3,
               metric='binary_logloss', min_data_in_leaf=243,
               min_gain_to_split=0.037469004918636514, n_estimators=918,
               num_leaves=30, objective='binary', seed=42, task='train',
               verbose=-10000000)

In [61]:
preds = tuned_model.predict_proba(X_test)
testloss = log_loss(y_test, preds)
testloss

0.031318579273911365

In [62]:
train_preds = tuned_model.predict_proba(X_train)
trainloss = log_loss(y_train, train_preds)
trainloss

0.028502436191172296

In [63]:
val_preds = tuned_model.predict_proba(X_val)
valloss = log_loss(y_val, val_preds)
valloss

0.03338523127850006

In [64]:
X_train.shape

(94168, 8)

# Submission Pipeline

In [65]:
# read the real test data from test.csv
test_data = pd.read_csv("test.csv")

In [66]:
X_testtest = test_data.drop(['id'], axis=1)
ID_test = test_data.id

In [67]:
#X_testtest = poly.fit_transform(X_testtest)

In [68]:
preds = tuned_model.predict_proba(X_testtest)

In [69]:
preds

array([[9.99919974e-01, 8.00259115e-05],
       [9.98654976e-01, 1.34502447e-03],
       [9.99809357e-01, 1.90642589e-04],
       ...,
       [9.99891304e-01, 1.08695882e-04],
       [9.47958479e-01, 5.20415207e-02],
       [1.49980629e-02, 9.85001937e-01]])

In [70]:
preds=  preds[:,1]

In [71]:
preds

array([8.00259115e-05, 1.34502447e-03, 1.90642589e-04, ...,
       1.08695882e-04, 5.20415207e-02, 9.85001937e-01])

In [72]:
preds.shape

(78377,)

In [73]:
# Save test predictions to file
submission = pd.DataFrame({'id': ID_test,
                       'Class': preds})
submission.to_csv('submission_optuna_lgbm.csv', index=False)